In [74]:
import pandas as pd
import numpy as np 
import folium
pd.set_option('display.max_columns', None)
data = pd.read_csv('traffic_accidents_denver.csv')

SOURCE: https://www.denvergov.org/opendata/dataset/city-and-county-of-denver-traffic-accidents
Period 1/1/2013 - 9/1/2020

In [75]:
data.head(1)

OBJECTID_1  INCIDENT_ID    OFFENSE_ID  OFFENSE_CODE  \
0           1   20193963.0  2.019400e+12          5401   

   OFFENSE_CODE_EXTENSION    TOP_TRAFFIC_ACCIDENT_OFFENSE  \
0                       0  TRAF - ACCIDENT - HIT & RUN      

  FIRST_OCCURRENCE_DATE LAST_OCCURRENCE_DATE   REPORTED_DATE  \
0        1/2/2019 20:50                  NaN  1/2/2019 21:01   

                INCIDENT_ADDRESS      GEO_X      GEO_Y     GEO_LON    GEO_LAT  \
0  W COLFAX AVE / N FEDERAL BLVD  3133517.0  1694947.0 -105.025221  39.740476   

   DISTRICT_ID  PRECINCT_ID NEIGHBORHOOD_ID  BICYCLE_IND  PEDESTRIAN_IND  \
0          1.0        121.0     West Colfax          0.0             0.0   

                                HARMFUL_EVENT_SEQ_1 HARMFUL_EVENT_SEQ_2  \
0  SIDE TO SIDE SAME DIRECTION WITH MV IN TRANSPORT                       

                                HARMFUL_EVENT_SEQ_3 ROAD_LOCATION  \
0  SIDE TO SIDE SAME DIRECTION WITH MV IN TRANSPORT    ON ROADWAY   

  ROAD_DESCRIPTION       ROAD_CONTOUR ROAD_CONDITION LIGHT_CONDITION  \
0  AT INTERSECTION  STRAIGHT ON-LEVEL            DRY    DARK-LIGHTED   

    TU1_VEHICLE_TYPE TU1_TRAVEL_DIRECTION TU1_VEHICLE_MOVEMENT  \
0  PASSENGER CAR/VAN                 WEST                OTHER   

  TU1_DRIVER_ACTION TU1_DRIVER_HUMANCONTRIBFACTOR TU1_PEDESTRIAN_ACTION  \
0  CARELESS DRIVING                                                       

    TU2_VEHICLE_TYPE TU2_TRAVEL_DIRECTION TU2_VEHICLE_MOVEMENT  \
0  PASSENGER CAR/VAN                 WEST       GOING STRAIGHT   

  TU2_DRIVER_ACTION TU2_DRIVER_HUMANCONTRIBFACTOR TU2_PEDESTRIAN_ACTION  \
0             OTHER                   NO APPARENT                         

   SERIOUSLY_INJURED  FATALITIES FATALITY_MODE_1 FATALITY_MODE_2  \
0                0.0         0.0                                   

  SERIOUSLY_INJURED_MODE_1 SERIOUSLY_INJURED_MODE_2  
0

In [77]:
data['GEO_LON'].isnull().sum()

7169

In [78]:
data['SERIOUSLY_INJURED'].isnull().sum()

325

In [79]:
data.shape

(181837, 45)

In [80]:
df = data

In [81]:
#add zero to null values for column below
df['SERIOUSLY_INJURED'] = df['SERIOUSLY_INJURED'].fillna(0)
df['SERIOUSLY_INJURED'].isnull().sum()

0

In [82]:
#add zero to null values for column below
df['FATALITIES'] = df['FATALITIES'].fillna(0)
df['FATALITIES'].isnull().sum()

0

In [84]:
#include only rows with X, Y coordinates
df = df.dropna(subset=['GEO_LON', 'GEO_LAT'])
df.shape
#verified 174,668 rows

(174668, 45)

In [85]:
#sum incidents grouped by coordinates
df_unique_coords = df.groupby(['GEO_LON', 'GEO_LAT']).agg({'SERIOUSLY_INJURED': 'sum', 'FATALITIES': 'sum', 'INCIDENT_ID': 'count'})
#Cols X and Y are now indices
#df_unique_coords.shape
df_unique_coords.head(3)

SERIOUSLY_INJURED  FATALITIES  INCIDENT_ID
GEO_LON     GEO_LAT                                              
-105.206197 39.665155                0.0         0.0           13
            39.665157                0.0         0.0           11
-105.109884 39.629896                1.0         0.0            9

In [102]:
#indexed and sorted by highest number of accidents by coordinates
df_unique_coords.sort_values(by='INCIDENT_ID', ascending=False, inplace=True)
dfloc = df_unique_coords.reset_index()
dfloc.head()
#idx 1 = i25 & 6th ave (highest number of accidents), idx 1 - I70  & Peoria st == idx 4 - i25 and 20th (most fatalities and serious injuries)

GEO_LON    GEO_LAT  SERIOUSLY_INJURED  FATALITIES  INCIDENT_ID
0 -105.013229  39.725677               13.0         1.0         1291
1 -104.847037  39.774007               26.0         4.0          805
2 -104.998902  39.711204               13.0         0.0          740
3 -105.004766  39.761159               12.0         1.0          674
4 -105.004334  39.760949               23.0         4.0          672

In [143]:
dfloc.to_csv('out.csv')

In [87]:
#lookup by coordinates
lookup = data[(data['GEO_LON']==-105.0043337) & (data['GEO_LAT']==39.76094894)]
lookup.head(1)

OBJECTID_1  INCIDENT_ID    OFFENSE_ID  OFFENSE_CODE  \
114         115   20193254.0  2.019330e+12          5441   

     OFFENSE_CODE_EXTENSION    TOP_TRAFFIC_ACCIDENT_OFFENSE  \
114                       0  TRAF - ACCIDENT                  

    FIRST_OCCURRENCE_DATE LAST_OCCURRENCE_DATE REPORTED_DATE  \
114               08:00.0                  NaN       08:00.0   

        INCIDENT_ADDRESS      GEO_X      GEO_Y     GEO_LON    GEO_LAT  \
114  I25 HWYNB / 20TH ST  3139350.0  1702436.0 -105.004334  39.760949   

     DISTRICT_ID  PRECINCT_ID NEIGHBORHOOD_ID  BICYCLE_IND  PEDESTRIAN_IND  \
114          1.0        113.0        Highland          0.0             0.0   

                    HARMFUL_EVENT_SEQ_1 HARMFUL_EVENT_SEQ_2  \
114  FRONT TO REAR WITH MV IN TRANSPORT                       

                    HARMFUL_EVENT_SEQ_3 ROAD_LOCATION  ROAD_DESCRIPTION  \
114  FRONT TO REAR WITH MV IN TRANSPORT    ON ROADWAY  NON INTERSECTION   

          ROAD_CONTOUR ROAD_CONDITION LIGHT_CONDITION TU1_VEHICLE_TYPE  \
114  STRAIGHT ON-GRADE            DRY       DAY LIGHT              SUV   

    TU1_TRAVEL_DIRECTION TU1_VEHICLE_MOVEMENT     TU1_DRIVER_ACTION  \
114                NORTH       GOING STRAIGHT  FOLLOWED TOO CLOSELY   

    TU1_DRIVER_HUMANCONTRIBFACTOR TU1_PEDESTRIAN_ACTION  \
114                   NO APPARENT                         

             TU2_VEHICLE_TYPE TU2_TRAVEL_DIRECTION TU2_VEHICLE_MOVEMENT  \
114  PICKUP TRUCK/UTILITY VAN                NORTH   STOPPED IN TRAFFIC   

    TU2_DRIVER_ACTION TU2_DRIVER_HUMANCONTRIBFACTOR TU2_PEDESTRIAN_ACTION  \
114             OTHER                   NO APPARENT                         

     SERIOUSLY_INJURED  FATALITIES FATALITY_MODE_1 FATALITY_MODE_2  \
114                0.0         0.0                                   

    SERIOUSLY_INJURED_MODE_1 SERIOUSLY_INJURED_MODE_2  
114

In [90]:
#333 incidents with fatalities
#dfloc[dfloc['FATALITIES'].gt(0)].index[-1]

In [89]:
#locations with fatalities
#333 incidents with fatalitie
f = dfloc[(dfloc['FATALITIES']>=1)].sort_values(by='FATALITIES', ascending=False)
f.shape

(333, 5)

In [91]:
#locations with serious injury that may also include fatalities. Some rows have 0 serious injury but has n fatalities.
s = dfloc[(dfloc['SERIOUSLY_INJURED']>=1) | (dfloc['FATALITIES']>=1)] \
    .sort_values(by='SERIOUSLY_INJURED', ascending=False)
s.shape

(2371, 5)

In [92]:
#locations with no serious injury and fatality, 26831 incidents
n = dfloc[(dfloc['SERIOUSLY_INJURED'] == 0) & (dfloc['FATALITIES'] == 0)]
#n.sort_index(ascending=False, inplace=True)
#n.sample(frac=1).reset_index(drop=True)
n.shape

(26831, 5)

In [93]:
#Denver coordinates
latitude = 39.7392358
longitude = -104.990251

In [99]:
# create map and display it
denver_map = folium.Map(location=[latitude, longitude], zoom_start=12)

# all accidents with at least one fatality (333 data points grouped by coordinates)
#top n spots
for lat, lng, in zip(f.GEO_LAT[:10], f.GEO_LON[:10]):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5, # define how big you want the circle markers to be
        color='yellow',
        fill=True,
        fill_color='red',
        fill_opacity=0.6
    ).add_to(denver_map)

# show map
denver_map

In [100]:
# create map and display it
denver_map = folium.Map(location=[latitude, longitude], zoom_start=12)

#Top n spots for serious injury that can include fatalities
for lat, lng, in zip(s.GEO_LAT[:10], s.GEO_LON[:10]):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5, # define how big you want the circle markers to be
        color='yellow',
        fill=True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(denver_map)

# show map
denver_map

In [101]:
# create map and display it
denver_map = folium.Map(location=[latitude, longitude], zoom_start=12)

# accidents with no serious injury or fatality, n random spots
for lat, lng, in zip(n['GEO_LAT'].sample(n = 50), n['GEO_LON'].sample(n = 50)):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5, # define how big you want the circle markers to be
        color='yellow',
        fill=True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(denver_map)

# show map
denver_map

In [103]:
# create map and display it
denver_map = folium.Map(location=[latitude, longitude], zoom_start=12)

#top n spots for total reported accidents
for lat, lng, in zip(dfloc['GEO_LAT'][:10], dfloc['GEO_LON'][:10]):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5, # define how big you want the circle markers to be
        color='yellow',
        fill=True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(denver_map)

# show map
denver_map

In [106]:
#balanced set csv file is created from other jupyter notebook. Below mapping ensures it has randomization in location. 
set1 = pd.read_csv('data_set.csv')
set1.head()

GEO_LON    GEO_LAT  MONTH ROAD_CONDITION LIGHT_CONDITION  \
0 -105.015348  39.730808      8            DRY    DARK-LIGHTED   
1 -105.031846  39.711128      6            WET    DARK-LIGHTED   
2 -104.998843  39.741401      5            DRY       DAY LIGHT   
3 -104.882975  39.777138     11            DRY       DAY LIGHT   
4 -104.865889  39.775633      3            DRY    DARK-LIGHTED   

         HUMAN_FACTOR  SERIOUSLY_INJURED  FATALITIES  BICYCLE_IND  \
0               OTHER                1.0         0.0          0.0   
1       DUI/DWAI/DUID                0.0         1.0          0.0   
2               OTHER                1.0         1.0          0.0   
3               OTHER                1.0         0.0          0.0   
4  AGGRESSIVE DRIVING                1.0         1.0          0.0   

   PEDESTRIAN_IND  INJURY_YN  
0             0.0          1  
1             1.0          1  
2             0.0          1  
3             0.0          1  
4             0.0          1

In [108]:
#if location is a feature, there should not be any nulls in the set --- TO DELETE
#s = set1.dropna(axis=0,subset=['GEO_Y'])
s.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7881 entries, 0 to 8199
Data columns (total 48 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   Unnamed: 0                     7881 non-null   int64  
 1   OBJECTID_1                     7881 non-null   int64  
 2   INCIDENT_ID                    7881 non-null   float64
 3   OFFENSE_ID                     7881 non-null   float64
 4   OFFENSE_CODE                   7881 non-null   int64  
 5   OFFENSE_CODE_EXTENSION         7881 non-null   int64  
 6   TOP_TRAFFIC_ACCIDENT_OFFENSE   7881 non-null   object 
 7   FIRST_OCCURRENCE_DATE          7881 non-null   object 
 8   LAST_OCCURRENCE_DATE           28 non-null     object 
 9   REPORTED_DATE                  7881 non-null   object 
 10  INCIDENT_ADDRESS               7881 non-null   object 
 11  GEO_X                          7881 non-null   float64
 12  GEO_Y                          7881 non-null   f

In [110]:
#MAP TO CHECK LOCATION DISTRO OF BALANCED SAMPLE SET
# create map and display it
denver_map = folium.Map(location=[latitude, longitude], zoom_start=12)

#top n spots for total reported accidents
for lat, lng, in zip(s['GEO_LAT'], s['GEO_LON']):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5, # define how big you want the circle markers to be
        color='yellow',
        fill=True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(denver_map)

# show map
denver_map